In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import time

from pgmpy.factors.discrete import TabularCPD
from pgmpy.inference import BeliefPropagation
from pgmpy.models import BayesianNetwork

import src.modelling_o2.o2satffa as o2satffa
import src.models.helpers as mh
import src.models.builders as mb
import src.inference.helpers as ih


plotsdir = "../../../../PlotsBreathe/O2_modelling/"

In [5]:
df = pd.read_excel(f"{plotsdir}airwayresistance_o2satffa_df.xlsx", index_col=0)
df.ID = df.ID.astype(str)
# To excel
# df.to_excel(f"{plotsdir}airwayresistance_o2satffa_df.xlsx")

In [6]:
df.head()

ID Date Recorded  FEV1  O2 Saturation  ecFEV1  Age   Sex  Height  \
0  101    2019-02-20  1.31           97.0    1.32   53  Male   173.0   
1  101    2019-02-21  1.29           96.0    1.32   53  Male   173.0   
2  101    2019-02-22  1.32           96.0    1.32   53  Male   173.0   
3  101    2019-02-23  1.28           97.0    1.33   53  Male   173.0   
4  101    2019-02-24  1.33           98.0    1.36   53  Male   173.0   

   Predicted FEV1  Healthy O2 Saturation  ecFEV1 % Predicted  \
0        3.610061               97.22596           36.564477   
1        3.610061               97.22596           36.564477   
2        3.610061               97.22596           36.564477   
3        3.610061               97.22596           36.841481   
4        3.610061               97.22596           37.672492   

   FEV1 % Predicted  O2 Saturation % Healthy  O2Sat % O2SatFFA      AR group  \
0         36.287474                99.767593        101.396449  (60.0, 80.0]   
1         35.733466                98.739061        100.351124  (60.0, 80.0]   
2         36.564477                98.739061        100.351124  (60.0, 80.0]   
3         35.456463                99.767593        101.396449  (60.0, 80.0]   
4         36.841481               100.796125        102.347739  (40.0, 60.0]   

   AR from ecFEV1 (%)  AR from FEV1 (%)  O2SatFFA from ecFEV1 (%)  \
0           60.838399         60.838399                 95.664100   
1           60.838399         62.296188                 95.664100   
2           60.838399         60.838399                 95.664100   
3           60.838399         62.296188                 95.664100   
4           59.381062         60.838399                 95.751993   

   O2SatFFA from FEV1 (%)  
0               95.664100  
1               95.564914  
2               95.664100  
3               95.564914  
4               95.664100

## Infer O2SatFFA after observing FEV1

In [7]:
def model_up_to_O2SatFFA(hfev1_prior, ho2sat_prior):
    """
    This is a point in time model with
    FEV1 = HFEV1 * (1-AR)
    O2SatFFA = HO2Sat * drop_func(AR)

    The model is the same as build_HFEV1_AB_FEV1(), with Airway Blockage renamed to Airway Resistance.
    """
    print("*** Building FEV1 and O2 point in time model ***")

    # Setting resolution of 0.05 to avoud rounding errors for AR
    HFEV1 = mh.variableNode("Healthy FEV1 (L)", 1, 6, 0.05, prior=hfev1_prior)
    AR = mh.variableNode("Airway Resistance (%)", 0, 90, 1, prior={"type": "uniform"})
    ecFEV1 = mh.variableNode("FEV1 (L)", 0, 6, 0.05, prior=None)
    # Lowest predicted FEV1 is 15% (AR = 1-predictedFEV1)
    HO2Sat = mh.variableNode(
        "Healthy O2 Saturation (%)", 90, 100, 0.5, prior=ho2sat_prior
    )
    # Highest drop is 93% (for AR = 90%), hence the lowest O2SatFFA is 90 * 0.93 = 83.7%
    O2SatFFA = mh.variableNode(
        "O2 Sat if fully functional alveoli (%)", 80, 100, 0.5, prior=None
    )

    prior_hfev1 = TabularCPD(
        variable=HFEV1.name,
        variable_card=len(HFEV1.bins),
        values=HFEV1.prior,
        evidence=[],
        evidence_card=[],
    )
    prior_ho2sat = TabularCPD(
        variable=HO2Sat.name,
        variable_card=len(HO2Sat.bins),
        values=HO2Sat.prior,
        evidence=[],
        evidence_card=[],
    )
    prior_ar = TabularCPD(
        variable=AR.name,
        variable_card=len(AR.bins),
        values=AR.prior,
        evidence=[],
        evidence_card=[],
    )
    cpt_fev1 = TabularCPD(
        variable=ecFEV1.name,
        variable_card=len(ecFEV1.bins),
        values=mh.calc_pgmpy_cpt_X_x_1_minus_Y(HFEV1, AR, ecFEV1),
        evidence=[HFEV1.name, AR.name],
        evidence_card=[len(HFEV1.bins), len(AR.bins)],
    )
    cpt_o2_sat_ffa = TabularCPD(
        variable=O2SatFFA.name,
        variable_card=len(O2SatFFA.bins),
        values=o2satffa.calc_cpt(O2SatFFA, HO2Sat, AR, debug=False),
        evidence=[HO2Sat.name, AR.name],
        evidence_card=[len(HO2Sat.bins), len(AR.bins)],
    )

    model = BayesianNetwork(
        [
            (HFEV1.name, ecFEV1.name),
            (AR.name, ecFEV1.name),
            (HO2Sat.name, O2SatFFA.name),
            (AR.name, O2SatFFA.name),
        ]
    )

    model.add_cpds(cpt_fev1, prior_ar, prior_hfev1, prior_ho2sat, cpt_o2_sat_ffa)

    model.check_model()
    inf_alg = BeliefPropagation(model)
    return (model, inf_alg, HFEV1, ecFEV1, AR, HO2Sat, O2SatFFA)

In [8]:
# Infer airway resistance using the model
# for id in df.ID.unique():
for id in ["101"]:
    df_for_ID = df[df.ID == id].copy().reset_index()
    print(f"\nRunning for ID {id}, with {len(df_for_ID)} observations")
    # Take one element of the df for ID at column height
    height = df_for_ID.Height[0]
    sex = df_for_ID.Sex[0]
    hfev1_prior = {
        "type": "default",
        "height": height,
        "age": df_for_ID.Age[0],
        "sex": sex,
    }
    ho2sat_prior = {
        "type": "default",
        "height": height,
        "sex": sex,
    }
    tic = time.time()
    (
        model,
        inf_alg,
        HFEV1,
        ecFEV1,
        AR,
        HO2Sat,
        O2SatFFA,
    ) = model_up_to_O2SatFFA(hfev1_prior, ho2sat_prior)
    print(f"model took {time.time() - tic} seconds to build")

    tic = time.time()
    df_for_ID["AR from FEV1"] = np.nan
    df_for_ID["AR from ecFEV1"] = np.nan
    df_for_ID["O2SatFFA from FEV1"] = np.nan
    df_for_ID["O2SatFFA from ecFEV1"] = np.nan
    fev1s_tmp = []
    ecfev1s_tmp = []
    for i in range(len(df_for_ID)):
        fev1_obs = df_for_ID.loc[i, "FEV1"]
        ecfev1_obs = df_for_ID.loc[i, "ecFEV1"]

        # FEV1
        if fev1_obs in fev1s_tmp:
            df_for_ID.loc[i, "AR from FEV1"] = df_for_ID.loc[
                df_for_ID["FEV1"] == fev1_obs, "AR from FEV1"
            ].values[0]
            df_for_ID.loc[i, "O2SatFFA from FEV1"] = df_for_ID.loc[
                df_for_ID["FEV1"] == fev1_obs, "O2SatFFA from FEV1"
            ].values[0]
        else:
            res_ar_for_fev1 = ih.infer(
                inf_alg, [AR], [[ecFEV1, fev1_obs]], show_progress=False
            )
            df_for_ID.loc[i, "AR from FEV1"] = AR.get_mean(res_ar_for_fev1.values)

            res_o2satffa_for_fev1 = ih.infer(
                inf_alg, [O2SatFFA], [[ecFEV1, fev1_obs]], show_progress=False
            )
            df_for_ID.loc[i, "O2SatFFA from FEV1"] = O2SatFFA.get_mean(
                res_o2satffa_for_fev1.values
            )

        # ecFEV1
        if ecfev1_obs in ecfev1s_tmp:
            df_for_ID.loc[i, "AR from ecFEV1"] = df_for_ID.loc[
                df_for_ID["ecFEV1"] == ecfev1_obs, "AR from ecFEV1"
            ].values[0]

            df_for_ID.loc[i, "O2SatFFA from ecFEV1"] = df_for_ID.loc[
                df_for_ID["ecFEV1"] == ecfev1_obs, "O2SatFFA from ecFEV1"
            ].values[0]
        else:
            res_ar_for_ecfev1 = ih.infer(
                inf_alg, [AR], [[ecFEV1, ecfev1_obs]], show_progress=False
            )
            df_for_ID.loc[i, "AR from ecFEV1"] = AR.get_mean(res_ar_for_ecfev1.values)

            res_o2satffa_for_ecfev1 = ih.infer(
                inf_alg, [O2SatFFA], [[ecFEV1, ecfev1_obs]], show_progress=False
            )
            df_for_ID.loc[i, "O2SatFFA from ecFEV1"] = O2SatFFA.get_mean(
                res_o2satffa_for_ecfev1.values
            )

        fev1s_tmp = np.append(fev1s_tmp, fev1_obs)
        ecfev1s_tmp = np.append(ecfev1s_tmp, ecfev1_obs)
    print(f"inference took {time.time() - tic} seconds to run")

    # Add to df
    df.loc[df.ID == id, "AR from ecFEV1 (%)"] = df_for_ID["AR from ecFEV1"].values
    df.loc[df.ID == id, "AR from FEV1 (%)"] = df_for_ID["AR from FEV1"].values

    df.loc[df.ID == id, "O2SatFFA from ecFEV1 (%)"] = df_for_ID[
        "O2SatFFA from ecFEV1"
    ].values
    df.loc[df.ID == id, "O2SatFFA from FEV1 (%)"] = df_for_ID[
        "O2SatFFA from FEV1"
    ].values

# IntegrationWarning: The maximum number of subdivisions (50) has been achieved.
# Happens when the results becomes too close to 0


Running for ID 101, with 816 observations
*** Building FEV1 and O2 point in time model ***
Defining gaussian prior with mu = 97.23, sigma = 1.0304


/var/folders/zq/v2r6yn111s3gpdf8lzf72xvw0000gn/T/ipykernel_1828/1820638602.py:24: DeprecationWarning: `product` is deprecated as of NumPy 1.25.0, and will be removed in NumPy 2.0. Please use `prod` instead.
  prior_hfev1 = TabularCPD(
/var/folders/zq/v2r6yn111s3gpdf8lzf72xvw0000gn/T/ipykernel_1828/1820638602.py:31: DeprecationWarning: `product` is deprecated as of NumPy 1.25.0, and will be removed in NumPy 2.0. Please use `prod` instead.
  prior_ho2sat = TabularCPD(
/var/folders/zq/v2r6yn111s3gpdf8lzf72xvw0000gn/T/ipykernel_1828/1820638602.py:38: DeprecationWarning: `product` is deprecated as of NumPy 1.25.0, and will be removed in NumPy 2.0. Please use `prod` instead.
  prior_ar = TabularCPD(
/Users/tristan.trebaol/Desktop/PhD/Code/phd/src/models/helpers.py:326: IntegrationWarning: The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position 

In [28]:
# For ID 101, 0.05 resolution takes 50s + 12s to run
df.head()

ID Date Recorded  FEV1  O2 Saturation  ecFEV1  Age   Sex  Height  \
0  101    2019-02-20  1.31           97.0    1.32   53  Male   173.0   
1  101    2019-02-21  1.29           96.0    1.32   53  Male   173.0   
2  101    2019-02-22  1.32           96.0    1.32   53  Male   173.0   
3  101    2019-02-23  1.28           97.0    1.33   53  Male   173.0   
4  101    2019-02-24  1.33           98.0    1.36   53  Male   173.0   

   Predicted FEV1  Healthy O2 Saturation  ecFEV1 % Predicted  \
0        3.610061               97.22596           36.564477   
1        3.610061               97.22596           36.564477   
2        3.610061               97.22596           36.564477   
3        3.610061               97.22596           36.841481   
4        3.610061               97.22596           37.672492   

   FEV1 % Predicted  O2 Saturation % Healthy  O2Sat % O2SatFFA      AR group  \
0         36.287474                99.767593        101.396449  (60.0, 80.0]   
1         35.733466                98.739061        100.351124  (60.0, 80.0]   
2         36.564477                98.739061        100.351124  (60.0, 80.0]   
3         35.456463                99.767593        101.396449  (60.0, 80.0]   
4         36.841481               100.796125        102.347739  (40.0, 60.0]   

   AR from ecFEV1 (%)  AR from FEV1 (%)  O2SatFFA from ecFEV1 (%)  \
0           60.838399         60.838399                 95.664100   
1           60.838399         62.296188                 95.664100   
2           60.838399         60.838399                 95.664100   
3           60.838399         62.296188                 95.664100   
4           59.381062         60.838399                 95.751993   

   O2SatFFA from FEV1 (%)  
0               95.664100  
1               95.564914  
2               95.664100  
3               95.564914  
4               95.664100

In [6]:
# Add title: inferred O2SatFFA from ecFEV1 vs. AR
title = "Inferred O2SatFFA vs. AR"
fig = px.scatter(
    df,
    x="Airway Resistance mean from ecFEV1 (%)",
    y="O2SatFFA from ecFEV1 (%)",
    title=title,
    hover_data=["ID", "ecFEV1"],
)
# Reduce marker size
fig.update_traces(marker=dict(size=2))
fig.update_layout(font=dict(size=10), title=title)
fig.show()

In [11]:
df["O2SatFFA from ecFEV1 (%)"]

0        95.664100
1        95.664100
2        95.664100
3        95.664100
4        95.751993
           ...    
20392    96.916740
20393    96.916740
20394    96.916740
20395    96.916740
20396    96.916740
Name: O2SatFFA from ecFEV1 (%), Length: 20397, dtype: float64

# Plot F2

In [3]:
df["O2Sat % O2SatFFA"] = df["O2 Saturation"] / df["O2SatFFA from ecFEV1 (%)"] * 100

In [9]:
title = (
    f"O2Sat % Inferred O2SatFFA vs. AR ({df.ID.nunique()} IDs, {len(df)} datapoints)"
)
fig = px.scatter(
    df,
    x="AR from ecFEV1 (%)",
    y="O2Sat % O2SatFFA",
    title=title,
    hover_data=["ID", "ecFEV1"],
)
# Reduce marker size
fig.update_traces(marker=dict(size=2), opacity=0.3)
fig.update_layout(font=dict(size=10))
fig.show()

In [17]:
import src.o2_fev1_analysis.partition as partition

O2_col = "O2Sat % O2SatFFA"
# O2_col = "O2SatFFA from ecFEV1 (%)"

# # Create 3 equally spaced bins for Airway Resistance
# df["AR group"] = partition.partition_in_n_equal_groups(
#     df["Airway Resistance mean from ecFEV1 (%)"], 5
# )

# Cut Airway Resistance into bins of 0-20, 20-40, 40-60, 60-80
df["AR group"] = pd.cut(
    df["AR from ecFEV1 (%)"],
    bins=np.arange(0, 100, 20),
    include_lowest=False,
)

group_labels = df["AR group"].unique()
print(f"AR groups: {group_labels}")

# Create subplot with 3 rows
fig = make_subplots(
    rows=len(group_labels) - 1, cols=1, shared_xaxes=True, vertical_spacing=0.02
)
# On first subplot add histogram of Drop from O2 Saturation FFA (%) for 1st AR group
for i in range(len(group_labels) - 1):
    fig.add_trace(
        go.Histogram(
            x=df[df["AR group"] == group_labels[i]][O2_col],
            name=f"Airway Resistance {group_labels[i]}",
            # Bin size of 1
            xbins=dict(start=75, end=110, size=0.2),
        ),
        row=i + 1,
        col=1,
    )

title = f"Distribution of {O2_col} for different Airway Resistance groups"
fig.update_layout(
    title=title,
    font=dict(size=10),
)
fig.update_xaxes(
    title_text="O2 Saturation in % of O2 Saturation if Fully Functional Alveoli",
    row=len(group_labels) - 1,
    col=1,
)
# Save
fig.write_image(f"{plotsdir}{title}.png")
fig.show()

AR groups: [(60.0, 80.0], (40.0, 60.0], (20.0, 40.0], (0.0, 20.0], NaN]
Categories (4, interval[int64, right]): [(0, 20] < (20, 40] < (40, 60] < (60, 80]]


In [27]:
# Scatter plot of O2SatFFA vs O2 Saturation
title = "O2SatFFA vs. O2 Saturation"
fig = px.scatter(
    df,
    y="O2SatFFA from ecFEV1 (%)",
    x="O2 Saturation",
    title=title,
    hover_data=["ID", "ecFEV1"],
)
# Reduce marker size
fig.update_traces(marker=dict(size=2))
fig.update_layout(font=dict(size=10), title=title)
fig.show()